In [1]:
with open('input.txt','r',encoding='utf-8') as f:
    text=f.read()

In [2]:
print(len(text))

1115394


In [3]:
print(text[:1000])

First Citizen:
Before we proceed any further, hear me speak.

All:
Speak, speak.

First Citizen:
You are all resolved rather to die than to famish?

All:
Resolved. resolved.

First Citizen:
First, you know Caius Marcius is chief enemy to the people.

All:
We know't, we know't.

First Citizen:
Let us kill him, and we'll have corn at our own price.
Is't a verdict?

All:
No more talking on't; let it be done: away, away!

Second Citizen:
One word, good citizens.

First Citizen:
We are accounted poor citizens, the patricians good.
What authority surfeits on would relieve us: if they
would yield us but the superfluity, while it were
wholesome, we might guess they relieved us humanely;
but they think we are too dear: the leanness that
afflicts us, the object of our misery, is as an
inventory to particularise their abundance; our
sufferance is a gain to them Let us revenge this with
our pikes, ere we become rakes: for the gods know I
speak this in hunger for bread, not in thirst for revenge.



In [4]:
chars=sorted(list(set(text)))
vocab_size=len(chars)
print(''.join(chars))
print(vocab_size)


 !$&',-.3:;?ABCDEFGHIJKLMNOPQRSTUVWXYZabcdefghijklmnopqrstuvwxyz
65


In [5]:
stoi={ch:i for i,ch in enumerate(chars)}
itos={i:ch for i,ch in enumerate(chars)}
encode=lambda s: [stoi[c] for c in s]
decode=lambda l: ''.join([itos[i] for i in l])
print(encode("hii there"))
print(decode(encode("hii there")))

[46, 47, 47, 1, 58, 46, 43, 56, 43]
hii there


In [6]:
import torch
data=torch.tensor(encode(text),dtype=torch.long)
print(data.shape,data.dtype)
print(data[:1000])

d:\anaconda3\envs\myenv\Lib\site-packages\torch\_subclasses\functional_tensor.py:258: UserWarning: Failed to initialize NumPy: DLL load failed while importing _multiarray_umath: 找不到指定的模块。 (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\builder\windows\pytorch\torch\csrc\utils\tensor_numpy.cpp:84.)
  cpu = _conversion_method_template(device=torch.device("cpu"))


torch.Size([1115394]) torch.int64
tensor([18, 47, 56, 57, 58,  1, 15, 47, 58, 47, 64, 43, 52, 10,  0, 14, 43, 44,
        53, 56, 43,  1, 61, 43,  1, 54, 56, 53, 41, 43, 43, 42,  1, 39, 52, 63,
         1, 44, 59, 56, 58, 46, 43, 56,  6,  1, 46, 43, 39, 56,  1, 51, 43,  1,
        57, 54, 43, 39, 49,  8,  0,  0, 13, 50, 50, 10,  0, 31, 54, 43, 39, 49,
         6,  1, 57, 54, 43, 39, 49,  8,  0,  0, 18, 47, 56, 57, 58,  1, 15, 47,
        58, 47, 64, 43, 52, 10,  0, 37, 53, 59,  1, 39, 56, 43,  1, 39, 50, 50,
         1, 56, 43, 57, 53, 50, 60, 43, 42,  1, 56, 39, 58, 46, 43, 56,  1, 58,
        53,  1, 42, 47, 43,  1, 58, 46, 39, 52,  1, 58, 53,  1, 44, 39, 51, 47,
        57, 46, 12,  0,  0, 13, 50, 50, 10,  0, 30, 43, 57, 53, 50, 60, 43, 42,
         8,  1, 56, 43, 57, 53, 50, 60, 43, 42,  8,  0,  0, 18, 47, 56, 57, 58,
         1, 15, 47, 58, 47, 64, 43, 52, 10,  0, 18, 47, 56, 57, 58,  6,  1, 63,
        53, 59,  1, 49, 52, 53, 61,  1, 15, 39, 47, 59, 57,  1, 25, 39, 56, 41,
      

In [7]:
#split up the data into train and validation sets
n=int(0.9*len(data))
train_data=data[:n]
val_data=data[n:]

In [8]:
block_size=8
train_data[:block_size+1]

tensor([18, 47, 56, 57, 58,  1, 15, 47, 58])

In [9]:
x=train_data[:block_size]
y=train_data[1:block_size+1]
for t in range(block_size):
    context=x[:t+1]
    target=y[t]
    print(f"when input is {context} the target: {target}")

when input is tensor([18]) the target: 47
when input is tensor([18, 47]) the target: 56
when input is tensor([18, 47, 56]) the target: 57
when input is tensor([18, 47, 56, 57]) the target: 58
when input is tensor([18, 47, 56, 57, 58]) the target: 1
when input is tensor([18, 47, 56, 57, 58,  1]) the target: 15
when input is tensor([18, 47, 56, 57, 58,  1, 15]) the target: 47
when input is tensor([18, 47, 56, 57, 58,  1, 15, 47]) the target: 58


In [10]:
torch.manual_seed(1337)
batch_size=64
block_size=256
max_iters=5000
eval_interval=500
learning_rate=3e-4
eval_iters=200
n_embd=384
device='cuda' if torch.cuda.is_available() else 'cpu'
dropout=0.2
n_head=6
n_layer=6

def get_batch(split):
    data=train_data if split=='train' else val_data
    ix=torch.randint(len(data)-block_size,(batch_size,))
    x=torch.stack([data[i:i+block_size] for i in ix])
    y=torch.stack([data[i+1:i+block_size+1]for i in ix])
    return x,y

xb,yb=get_batch('train')
print('inputs:')
print(xb.shape)
print(xb)
print('targets:')
print(yb.shape)
print(yb)
print('-------')

for b in range(batch_size):
    for t in range(block_size):
        context=xb[b, :t+1]
        target=yb[b,t]
        print(f"when input is {context.tolist()} the target: {target}")

inputs:
torch.Size([64, 256])
tensor([[ 0, 26, 53,  ..., 56, 43, 47],
        [60, 43, 56,  ..., 56,  1, 41],
        [26, 21, 33,  ..., 26, 21, 13],
        ...,
        [ 5, 57,  1,  ...,  1, 35, 47],
        [56, 53, 53,  ..., 59, 50, 42],
        [42, 47, 56,  ..., 39, 56,  1]])
targets:
torch.Size([64, 256])
tensor([[26, 53, 58,  ..., 43, 47, 45],
        [43, 56,  1,  ...,  1, 41, 53],
        [21, 33, 31,  ..., 21, 13, 10],
        ...,
        [57,  1, 52,  ..., 35, 47, 50],
        [53, 53, 58,  ..., 50, 42,  1],
        [47, 56, 43,  ..., 56,  1, 51]])
-------
when input is [0] the target: 26
when input is [0, 26] the target: 53
when input is [0, 26, 53] the target: 58
when input is [0, 26, 53, 58] the target: 1
when input is [0, 26, 53, 58, 1] the target: 19
when input is [0, 26, 53, 58, 1, 19] the target: 50
when input is [0, 26, 53, 58, 1, 19, 50] the target: 53
when input is [0, 26, 53, 58, 1, 19, 50, 53] the target: 59
when input is [0, 26, 53, 58, 1, 19, 50, 53, 59] the

In [11]:
import torch
import torch.nn as nn
from torch.nn import functional as F
torch.manual_seed(1337)


In [12]:
class Head(nn.Module):

    def __init__(self, head_size) :
        super().__init__()
        self.key=nn.Linear(n_embd,head_size,bias=False)
        self.query=nn.Linear(n_embd,head_size,bias=False)
        self.value=nn.Linear(n_embd,head_size,bias=False)
        self.register_buffer('tril',torch.tril(torch.ones(block_size,block_size)))
        self.dropout=nn.Dropout(dropout)

    def forward(self,x):
        B,T,C=x.shape
        k=self.key(x)  
        q=self.query(x)
        wei=q@k.transpose(-2,-1)  #(B,T,16)@(B,16,T)-->(B,T,T)
        wei=wei.masked_fill(self.tril[:T,:T]==0,float('-inf'))  #mask效果
        wei=F.softmax(wei,dim=-1)
        wei=self.dropout(wei)
        v=self.value(x)
        out=wei@v
        return out
a=Head(head_size=16)
x=torch.randn(4,8,384)
print(a(x)) 

tensor([[[ 0.0000e+00,  0.0000e+00,  0.0000e+00,  0.0000e+00,  0.0000e+00,
           0.0000e+00,  0.0000e+00,  0.0000e+00,  0.0000e+00,  0.0000e+00,
           0.0000e+00,  0.0000e+00,  0.0000e+00,  0.0000e+00,  0.0000e+00,
           0.0000e+00],
         [-3.9155e-01,  4.8452e-02, -2.3787e-01,  3.1425e-01,  4.0081e-02,
           4.0673e-01, -9.0618e-01,  1.0578e-01,  9.9572e-02,  5.0143e-01,
           2.3062e-01,  5.3378e-01, -5.5727e-01,  7.2355e-01,  5.2724e-02,
           8.3972e-01],
         [-6.3378e-01, -1.1314e-01, -4.4978e-02,  3.6332e-02,  1.8773e-01,
           2.5859e-01, -1.2039e+00, -3.0536e-02,  8.2339e-03,  1.2468e-01,
           1.7726e-01,  7.0380e-01, -2.5755e-01,  6.5314e-01, -6.5175e-02,
           8.8954e-01],
         [-2.4470e-01, -2.8661e-01, -1.7910e-02,  3.7684e-01,  1.4022e-01,
           3.6490e-01, -5.2504e-01,  3.4870e-02,  1.0778e-01,  2.9008e-01,
          -2.1445e-02,  3.1357e-01, -1.6720e-01,  6.8957e-01, -1.4647e-01,
           3.2633e-01],
    

In [13]:
x=torch.randn(3,4,5)
print(x)
B,T,C=x.shape
A=Head(16)
A.tril[:T,:T]==0

tensor([[[-0.3092,  1.9906, -1.8892,  1.2138,  0.3659],
         [ 0.9029, -2.4558, -0.6335, -0.5376, -1.6698],
         [ 0.0331,  0.2855, -0.1585,  0.4562, -1.0951],
         [-2.2030,  1.0600,  0.8446,  1.5482, -0.3334]],

        [[ 1.7645,  0.5268, -1.0477,  0.3935,  1.0462],
         [ 0.8407,  0.2604, -0.0638, -0.7693, -0.1004],
         [ 0.0712, -0.8578,  0.5832, -1.7698, -0.2629],
         [ 0.7645,  1.0361,  2.2900, -0.0749, -0.1606]],

        [[ 2.1959, -1.4091, -1.1780,  1.0723,  2.5443],
         [ 0.3263, -0.1924,  0.8313, -0.2719,  0.6706],
         [ 0.7507, -1.4718, -0.3152, -0.4303, -0.1092],
         [-0.8928,  0.8386, -0.3785, -0.3733,  0.2004]]])


tensor([[False,  True,  True,  True],
        [False, False,  True,  True],
        [False, False, False,  True],
        [False, False, False, False]])

In [14]:
class MultiHeadAttention(nn.Module):
    def __init__(self, num_heads, head_size) :
        super().__init__()
        self.heads=nn.ModuleList([Head(head_size) for  _ in range(num_heads)])
        self.proj=nn.Linear(n_embd,n_embd)
        self.dropout=nn.Dropout(dropout)

    def forward(self,x):
        out=torch.cat([h(x) for h in self.heads],dim=-1)
        out=self.dropout(self.proj(out))  
        return out

In [15]:
class FeedFoward(nn.Module):
    def __init__(self,n_embd):
        super().__init__()
        self.net=nn.Sequential(
            nn.Linear(n_embd,n_embd*4),
            nn.ReLU(),
            nn.Linear(4*n_embd,n_embd),  #？？
            nn.Dropout(dropout),
        )

    def forward(self,x):
        return self.net(x)

In [16]:
class Block(nn.Module):

    def __init__(self, n_embd, n_head) :
        super().__init__()
        head_size=n_embd//n_head
        self.sa=MultiHeadAttention(n_head,head_size)
        self.ffwd=FeedFoward(n_embd)
        self.ln1=nn.LayerNorm(n_embd)
        self.ln2=nn.LayerNorm(n_embd)

    def forward(self,x):
        x=self.sa(self.ln1(x))
        x=self.ffwd(self.ln2(x))
        return x

In [17]:
torch.manual_seed(1337)
class BigramlanguageModule(nn.Module):

    def __init__(self):
        super().__init__()
        self.token_embedding_table=nn.Embedding(vocab_size,n_embd)
        self.position_embedding_table=nn.Embedding(block_size,n_embd)  
        self.blocks=nn.Sequential(
            Block(n_embd,n_head=4),
            Block(n_embd,n_head=4),
            Block(n_embd,n_head=4),  #？？
        )
        self.lm_head=nn.Linear(n_embd,vocab_size)  #？？
    
    def forward(self,idx,targets=None):
        B,T=idx.shape
        
        tok_emb=self.token_embedding_table(idx)
        pos_emb=self.position_embedding_table(torch.arange(T,device=device)) 
        x=tok_emb+pos_emb
        x=self.blocks(x)
        logits=self.lm_head(x)

        if targets is None:
            loss = None
        else:
            B,T,C=logits.shape
            logits=logits.view(B*T,C)
            targets=targets.view(B*T)
            loss=F.cross_entropy(logits,targets)

        return logits,loss
    
    def generate(self,idx,max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond=idx[:,-block_size:]
            logits,loss=self(idx_cond)
            logits=logits[:,-1,:] 
            probs=F.softmax(logits,dim=-1)
            idx_next=torch.multinomial(probs,num_samples=1)  #(B,1)
            idx=torch.cat((idx,idx_next),dim=1)
        return idx




m=BigramlanguageModule()
logits,loss=m(xb,yb)
print(logits.shape)
print(loss)   #?为什么是一个数
print(decode(m.generate(idx=torch.zeros((1,1),dtype=torch.long),max_new_tokens=100)[0].tolist()))

torch.Size([16384, 65])
tensor(4.2220, grad_fn=<NllLossBackward0>)

tSA?xL$WJ-QHEFOQa.g:GQ&g?fvE.fe
Akq toa:ibrnrU BTfq$-K
!cc3N$hIECmT,ZQsuhCa
vGS.!ePJ;!nxR&rfXcKIDffM


In [18]:
optimizer=torch.optim.AdamW(m.parameters(),lr=1e-3)

In [19]:
for steps in range(10):
    xb,yb=get_batch('train')

    logits,loss=m(xb,yb)
    optimizer.zero_grad(set_to_none=True)
    loss.backward()
    optimizer.step()
print(loss.item())

3.3746252059936523


In [20]:
print(decode(m.generate(idx=torch.zeros((1,1),dtype=torch.long),max_new_tokens=50)[0].tolist()))


l GianIraE
dgded ai
o io :esEdfdnAsrtJU'hrnA;ay h

